# LIBRARIES


In [38]:
# LIBRARIES #

import numpy as np
import pydicom as dcm

import struct
import subprocess
from os.path import basename

from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.models import LinearColorMapper, BasicTicker, ColorBar, Plot, CustomJS, ColumnDataSource, Rect
from bokeh.layouts import row, gridplot, column
from bokeh.models.widgets import Slider

output_notebook()


Loading BokehJS ...

# Functions

In [2]:
# DRAWS THE IMAGE:

def drawImg(img, nbpixx, nbpixy, nbslices, plotwidth=500, titlegraph='Graph', titlebar='Counts/s'):
    # Characteristics of the image:
    _min, _max = np.amin(img), np.amax(img)
    
    # Displays the dose image (p1):
    color_mapper = LinearColorMapper(palette="Viridis256", low=0, high=_max)

    color_bar = ColorBar(color_mapper=color_mapper, ticker=BasicTicker(),
                     label_standoff=12, border_line_color=None, location=(0,0),
                     title=titlebar)

    p1 = figure(plot_width=int(plotwidth*1.1), plot_height=int(plotwidth*nbpixy/nbpixx), 
                    x_range=(0,nbpixx), y_range=(0,nbpixy), 
                    title=titlegraph, toolbar_location="above")

    fig1_source = ColumnDataSource(data=dict(img=[img[int(nbslices/2),:,:]], x=[0], y=[0],
                    dw=[nbpixx], dh=[nbpixy]))

    p1.image(image='img', x='x', y='y', dw='dw', dh='dh', 
                     source=fig1_source, color_mapper=color_mapper)

    p1.add_layout(color_bar, 'right')


    # callback functions:
    callback_sliderz = CustomJS(args=dict(source=fig1_source), code="""
        var f = nbSlice_slider.value;
        //console.log(f);
        var data = source.data;
        var img = data['img'][0];
        var width = data['dw'];
        var height = data['dh'];
        //console.log(img[64*128+64]);
        for (i = 0; i < width; i++) {
            for (j = 0; j < height; j++) {
                img[j*width+i] = img3D[f][j][i];
            }
        }    
        source.change.emit();
    """)


    # plotting inline:
    sliderz = Slider(start=0, end=nbslices, value=int(nbslices/2), step=1, title="Slice nb", callback=callback_sliderz)
    callback_sliderz.args["nbSlice_slider"] = sliderz

    callback_sliderz.args["img3D"] = img #ColumnDataSource()

    # Organizing the graphs:
    grid = gridplot([[p1, sliderz]])

    show(grid)

In [8]:
# READS THE HEADER FILE OF A SINOGRAM FILE

def readSgHeader(filepath, filename):
    
    dataf = ''
    nbofevents = 0
    sizex = 0
    sizey = 0
    nbofangles = 0
    nbBytesPix = 0
  
    with open(filepath+filename) as f:
        for line in f:
            value = line.strip().split(': ')
            if 'Data filename' in value[0]:
                dataf = value[1]
            if 'Number of bins' in value[0]:
                sizex = value[1].split(',')[0]
                sizey = value[1].split(',')[1]
            if 'Number of events' in value[0]:
                nbofevents = value[1]
            if 'Number of projections' in value[0]:
                nbofangles = value[1]
               
    return dataf, int(nbofevents), int(sizex), int(sizey), int(nbofangles)

In [4]:
# READS THE HEADER FILE OF AN IMAGE FILE

def readImgHeader(filepath, filename):
    
    dataoffset = 0
    nbofbytesperpix = 4
    sizex = 0
    sizey = 0
    sizez = 0
    rescaleoffset = 0
    rescaleslope = 1
    
    with open(filepath+filename) as f:
        for line in f:
            value = line.strip().split(' := ')
            if 'name of data file' in value[0]:
                imgfilename = value[1]
            elif 'data offset in bytes' in value[0]:
                dataoffset = value[1]
            elif 'number of bytes per pixel' in value[0]:
                nbofbytesperpix = value[1]
            elif 'matrix size [1]' in value[0]:
                sizex = value[1]
            elif 'matrix size [2]' in value[0]:
                sizey = value[1]
            elif 'matrix size [3]' in value[0]:
                sizez = value[1]
            elif 'data rescale offset' in value[0]:
                rescaleoffset = value[1]
            elif 'data rescale slope' in value[0]:
                rescaleslope = value[1]
               
    return imgfilename, int(dataoffset), int(nbofbytesperpix), int(sizex), int(sizey), int(sizez), int(rescaleoffset), int(rescaleslope)

In [29]:
# READS THE BINARY FILE OF A SINOGRAM:

def readSgBinaryFile(filepath, filename, sizex, sizey, nbofangles):
    
    sg = np.zeros((sizex, sizey, nbofangles))    
    with open(filepath+filename, "rb") as f:
        for i in range(sizex):
            for j in range(sizey):
                for theta in range(nbofangles):
                    data = f.read(16)
                    (time, s, binID, projID) = struct.unpack("<ifii", data)
                    sg[theta, j, i] = s
    
    return sg

In [16]:
# READS THE BINARY FILE OF AN IMAGE:

def readImgBinaryFile(filepath, filename, sizex, sizey, sizez, rescaleoffset, rescaleslope):
    
    imgtmp = np.fromfile(FILEPATH+filename, dtype=np.float32)

    img = np.zeros((sizez, sizey, sizex))
    for i in range(sizex):
        for j in range(sizey):
            for k in range(sizez):
                img[k, j, i] = imgtmp[k*sizex*sizey+j*sizex+i] * rescaleslope + rescaleoffset
    
    return img

# Processing

In [36]:
# reading a sinogram input file:

FILEPATH = "imgs/interfile/"
FILENAME = "sg.cdh"

sgFileName, nbOfEvents, sizex, sizey, nbOfAngles = readSgHeader(FILEPATH, FILENAME)

print('Binary file:', sgFileName)
print('Nb of events:', nbOfEvents)
print('size: (' + str(sizex) + "," + str(sizey) + "," + str(nbOfAngles) + ")")

sg = readSgBinaryFile(FILEPATH, sgFileName, sizex, nbOfAngles, sizey)
print("\n  --> Binary Image File rEAD !")

Binary file: sg.cdf
Nb of events: 983040
size: (128,128,60)

  --> Binary Image File rEAD !


In [37]:
#drawImg(sg, sizex, sizey, nbOfAngles)



In [ ]:
# reading an image input file:

FILEPATH = "C:/Users/00004436/Documents/castor_v3.0.1/castor_benchmark_v3_spect_histogram/"
FILENAME = "imgs/reconsmysg_it4.hdr"

imgfilename, doffset, nbbytesperpix, sizex, sizey, sizez, rescaleoffset, rescaleslope =  readImgHeader(FILEPATH, FILENAME)

print('Binary file:', imgfilename)
print('Offset data:', doffset)
print('Bytes per pix:', nbbytesperpix)
print('size: (' + str(sizex) + "," + str(sizey) + "," + str(sizez) + ")")
print('Rescale offset:', rescaleoffset)
print('Rescale slope:', rescaleslope)

img = readImgBinaryFile(FILEPATH, imgfilename, sizex, sizey, sizez, rescaleoffset, rescaleslope)

            
print("\n  --> Binary Image File rEAD !")

In [ ]:
drawImg(img, sizex, sizey, sizez)